# bigrams_trigrams

Script to create unigrams, bigrams and trigrams, aggregate them based on the feature type (WTC, SC, IC) and merge them into a final table.


In [1]:
import pandas as pd
pd.set_option('display.max_columns', None)

## Load data

In [2]:
data = pd.read_pickle("../data/df.pickle") # "data/df.pickle"

In [3]:
data.head()

lang uniform_id itemid  sentnum  ianum      ia          ia_id        TF  \
0   ee       ee_1      1      1.0    1.0  Samuel  1_0001_Samuel  0.059849   
1   ee       ee_1      1      1.0    2.0  Morse,  1_0002_Morse,  0.044309   
2   ee       ee_1      1      1.0    3.0    best    1_0003_best  0.000000   
3   ee       ee_1      1      1.0    4.0   known   1_0004_known  0.043049   
4   ee       ee_1      1      1.0    5.0   today   1_0005_today  0.045359   

         FP        FF  
0  0.059849  0.023100  
1  0.044309  0.044309  
2  0.000000  0.000000  
3  0.043049  0.043049  
4  0.045359  0.045359

## Get unigrams based on data from one language
## Use unigrams to generate bigrams and trigrams

In [4]:
languages = data['lang'].unique()

In [5]:
languages

array(['ee', 'en', 'fi', 'ge', 'he', 'it', 'sp'], dtype=object)

In [6]:
lang_dict = {elem : pd.DataFrame() for elem in languages}

for key in lang_dict.keys():
    lang_dict[key] = data[:][data.lang == key]

In [7]:
unigrams = sorted(set(lang_dict['fi']['ia_id']))

In [8]:
text = " ".join(sorted(set(lang_dict['fi']['ia_id'])))

In [9]:
bigrams = [b for b in zip(unigrams[:-1], unigrams[1:])]

In [10]:
bigrams[:5]

[('1_0001_Samuel', '1_0002_Morse,'),
 ('1_0002_Morse,', '1_0003_best'),
 ('1_0003_best', '1_0004_known'),
 ('1_0004_known', '1_0005_today'),
 ('1_0005_today', '1_0006_as')]

In [11]:
trigrams = [t for t in zip(unigrams[:-2], unigrams[1:-1], unigrams[2:])]

In [12]:
trigrams[:5]

[('1_0001_Samuel', '1_0002_Morse,', '1_0003_best'),
 ('1_0002_Morse,', '1_0003_best', '1_0004_known'),
 ('1_0003_best', '1_0004_known', '1_0005_today'),
 ('1_0004_known', '1_0005_today', '1_0006_as'),
 ('1_0005_today', '1_0006_as', '1_0007_the')]

### Helper

In [13]:
def add_header(df, header_name):
    """
    header_name - 'TF', 'FF', 'TF_bi', etc.
    """
    header = [[header_name for i in range(len(df.columns))], list(df.columns)]
    df.columns = header
    #return df

### Get tags (for SC)

In [14]:
tags = pd.read_pickle("../data/df_tags.pickle")
POS_mapper = pd.Series(tags.POS_tag.values, index=tags.ia_id).to_dict()
PTB_mapper = pd.Series(tags.PTB_tag.values, index=tags.ia_id).to_dict()
UD_mapper = pd.Series(tags.UD_tag.values, index=tags.ia_id).to_dict()
IC_mapper = pd.Series(tags.IC_tag.values, index=tags.ia_id).to_dict()
random_mapper = pd.Series(tags.random.values, index=tags.ia_id).to_dict()

In [15]:
def map_unigrams(df_original, mapper):
    dataframes = []
    for i in ["TF", "FP", "FF"]:
        df = df_original[i].copy().reset_index()
        df = pd.melt(df, id_vars="uniform_id", value_vars = df.columns)
        df.ia_id = df.ia_id.apply(lambda x: mapper[x])
        df = pd.pivot_table(df, values="value", index="uniform_id", columns="ia_id")
        add_header(df, i)
        dataframes.append(df)
    return pd.concat(dataframes, axis=1)

def map_bigrams(df, mapper):
    df = df.copy().reset_index()
    df = pd.melt(df, id_vars="uniform_id", value_vars = df.columns)
    if type(mapper['1_0001_Samuel']) == int:
        df.variable = df.variable.apply(lambda x: mapper[x.split(":")[0]] + mapper[x.split(":")[1]])
    else:
        df.variable = df.variable.apply(lambda x: (mapper[x.split(":")[0]], mapper[x.split(":")[1]]))
    df = pd.pivot_table(df, values="value", index="uniform_id", columns="variable")
    return df

def map_trigrams(df, mapper):
    df = df.copy().reset_index()
    df = pd.melt(df, id_vars="uniform_id", value_vars = df.columns)
    if type(mapper['1_0001_Samuel']) == int:
        df.variable = df.variable.apply(lambda x: mapper[x.split(":")[0]] + mapper[x.split(":")[1]] + mapper[x.split(":")[2]])
    else:
        df.variable = df.variable.apply(lambda x: (mapper[x.split(":")[0]], mapper[x.split(":")[1]], mapper[x.split(":")[2]]))
    df = pd.pivot_table(df, values="value", index="uniform_id", columns="variable")
    return df

## Use pivoted data to get values for bigrams and trigrams

### Load data

In [16]:
data_pivoted = pd.read_pickle("../data/df_pivoted.pickle") # "data/df_pivoted.pickle"

In [17]:
data_pivoted['TF'].head()

ia_id       1_0001_Samuel  1_0002_Morse,  1_0003_best  1_0004_known  \
uniform_id                                                            
ee_1             0.059849       0.044309     0.000000      0.043049   
ee_12            0.147014       0.099674     0.000000      0.128339   
ee_16            0.011184       0.080913     0.000000      0.032350   
ee_19            0.072944       0.062334     0.065539      0.038904   
ee_2             0.055410       0.071429     0.029421      0.038411   

ia_id       1_0005_today  1_0006_as  1_0007_the  1_0008_inventor  1_0009_of  \
uniform_id                                                                    
ee_1            0.045359   0.000000    0.049769         0.043679   0.028139   
ee_12           0.000000   0.000000    0.000000         0.062975   0.000000   
ee_16           0.012084   0.012009    0.024469         0.046386   0.000000   
ee_19           0.057250   0.035146    0.052940         0.040893   0.018015   
ee_2            0.049689   0.028114    0.000000         0.081890   0.000000   

ia_id       1_0010_Morse  1_0011_Code  1_0012_and  1_0013_one  1_0014_of  \
uniform_id                                                                 
ee_1            0.041789     0.000000    0.040739    0.049349   0.000000   
ee_12           0.049077     0.031488    0.000000    0.000000   0.046037   
ee_16           0.052616     0.037079    0.022367    0.015012   0.000000   
ee_19           0.069297     0.085875    0.000000    0.010942   0.000000   
ee_2            0.043969     0.062439    0.000000    0.000000   0.000000   

ia_id       1_0015_the  1_0016_inventors  1_0017_of  1_0018_the  \
uniform_id                                                        
ee_1          0.039899          0.034649   0.039689    0.049139   
ee_12         0.036265          0.019110   0.000000    0.000000   
ee_16         0.016138          0.098401   0.015762    0.035427   
ee_19         0.016468          0.034151   0.015363    0.000000   
ee_2          0.050997          0.097581   0.000000    0.024845   

ia_id       1_0019_telegraph,  1_0020_was  1_0021_originally  1_0022_a  \
uniform_id                                                               
ee_1                 0.051029    0.019110           0.062789  0.000000   
ee_12                0.087296    0.000000           0.143322  0.000000   
ee_16                0.262929    0.034302           0.029873  0.009532   
ee_19                0.034593    0.021662           0.080349  0.000000   
ee_2                 0.053449    0.114090           0.074534  0.000000   

ia_id       1_0023_prominent  1_0024_painter.  1_0025_While  1_0026_he  \
uniform_id                                                               
ee_1                0.143847         0.113818      0.040170   0.015013   
ee_12               0.105103         0.044300      0.000000   0.032554   
ee_16               0.065901         0.085266      0.022401   0.013286   
ee_19               0.115385         0.071950      0.051067   0.006286   
ee_2                0.059660         0.064073      0.000000   0.018334   

ia_id       1_0027_was  1_0028_always  1_0029_interested  1_0030_in  \
uniform_id                                                            
ee_1          0.102252       0.081152           0.063806   0.000000   
ee_12         0.000000       0.000000           0.029271   0.000000   
ee_16         0.010783       0.009771           0.060054   0.011379   
ee_19         0.040048       0.015327           0.031996   0.000000   
ee_2          0.000000       0.020200           0.018334   0.000000   

ia_id       1_0031_technology  1_0032_and  1_0033_studied  1_0034_electrical  \
uniform_id                                                                     
ee_1                 0.046054    0.000000        0.044938           0.025462   
ee_12                0.023116    0.000000        0.040624           0.027219   
ee_16                0.094310    0.015252        0.049926           0.052845   
ee_19    

In [18]:
data_unigrams = data_pivoted

In [19]:
tf_dict = {}
fp_dict = {}
ff_dict = {}
for bigram in bigrams:
    bigram_str = ":".join(bigram)
    tf_dict[bigram_str] = data_pivoted['TF'][bigram[0]]+data_pivoted['TF'][bigram[1]]
    fp_dict[bigram_str] = data_pivoted['FP'][bigram[0]]+data_pivoted['FP'][bigram[1]]
    ff_dict[bigram_str] = data_pivoted['FF'][bigram[0]]+data_pivoted['FF'][bigram[1]]

In [20]:
## Dataframes with bigrams (separately for TF, FP and FF)
data_tf_bigrams = pd.DataFrame.from_dict(tf_dict)
data_fp_bigrams = pd.DataFrame.from_dict(fp_dict)
data_ff_bigrams = pd.DataFrame.from_dict(ff_dict)

In [21]:
data_tf_bigrams.head(5)

1_0001_Samuel:1_0002_Morse,  1_0002_Morse,:1_0003_best  \
uniform_id                                                           
ee_1                           0.104158                   0.044309   
ee_12                          0.246688                   0.099674   
ee_16                          0.092096                   0.080913   
ee_19                          0.135279                   0.127874   
ee_2                           0.126839                   0.100850   

            1_0003_best:1_0004_known  1_0004_known:1_0005_today  \
uniform_id                                                        
ee_1                        0.043049                   0.088408   
ee_12                       0.128339                   0.128339   
ee_16                       0.032350                   0.044434   
ee_19                       0.104443                   0.096154   
ee_2                        0.067833                   0.088101   

            1_0005_today:1_0006_as  1_0006_as:1_0007_the  \
uniform_id                                                 
ee_1                      0.045359              0.049769   
ee_12                     0.000000              0.000000   
ee_16                     0.024094              0.036478   
ee_19                     0.092396              0.088086   
ee_2                      0.077803              0.028114   

            1_0007_the:1_0008_inventor  1_0008_inventor:1_0009_of  \
uniform_id                                                          
ee_1                          0.093448                   0.071819   
ee_12                         0.062975                   0.062975   
ee_16                         0.070855                   0.046386   
ee_19                         0.093833                   0.058908   
ee_2                          0.081890                   0.081890   

            1_0009_of:1_0010_Morse  1_0010_Morse:1_0011_Code  \
uniform_id                                                     
ee_1                      0.069929                  0.041789   
ee_12                     0.049077                  0.080565   
ee_16                     0.052616                  0.089695   
ee_19                     0.087312                  0.155172   
ee_2                      0.043969                  0.106407   

            1_0011_Code:1_0012_and  1_0012_and:1_0013_one  \
uniform_id                                                  
ee_1                      0.040739               0.090088   
ee_12                     0.031488               0.000000   
ee_16                     0.059446               0.037379   
ee_19                     0.085875               0.010942   
ee_2                      0.062439               0.000000   

            1_0013_one:1_0014_of  1_0014_of:1_0015_the  \
uniform_id                                               
ee_1                    0.049349              0.039899   
ee_12                   0.046037              0.082302   
ee_16                   0.015012              0.016138   
ee_19                   0.010942              0.016468   
ee_2                    0.000000              0.050997   

            1_0015_the:1_0016_inventors  1_0016_inventors:1_0017_of  \
uniform_id                                                            
ee_1                           0.074549                    0.074339   
ee_12                          0.055375                    0.019110   
ee_16                          0.114539                    0.114163   
ee_19                          0.050619                    0.049514   
ee_2                           0.148578                    0.097581   

            1_0017_of:1_0018_the  1_0018_the:1_0019_telegraph,  \
uniform_id                                                       
ee_1                    0.088828                      0.100168   
ee_12                   0.000000                      0.087296   
ee_16                   0.051190                      0.298356   
ee_19                   0.015363  

In [22]:
tf_dict_trigrams = {}
fp_dict_trigrams = {}
ff_dict_trigrams = {}
for trigram in trigrams:
    trigram_str = ":".join(trigram)
    tf_dict_trigrams[trigram_str] = data_pivoted['TF'][trigram[0]]+data_pivoted['TF'][trigram[1]]+data_pivoted['TF'][trigram[2]]
    fp_dict_trigrams[trigram_str] = data_pivoted['FP'][trigram[0]]+data_pivoted['FP'][trigram[1]]+data_pivoted['FP'][trigram[2]]
    ff_dict_trigrams[trigram_str] = data_pivoted['FF'][trigram[0]]+data_pivoted['FF'][trigram[1]]+data_pivoted['FF'][trigram[2]]

In [23]:
## Dataframes with trigrams (separately for TF, FP and FF)
data_tf_trigrams = pd.DataFrame.from_dict(tf_dict_trigrams)
data_fp_trigrams = pd.DataFrame.from_dict(fp_dict_trigrams)
data_ff_trigrams = pd.DataFrame.from_dict(ff_dict_trigrams)

In [24]:
data_tf_trigrams.head()

1_0001_Samuel:1_0002_Morse,:1_0003_best  \
uniform_id                                            
ee_1                                       0.104158   
ee_12                                      0.246688   
ee_16                                      0.092096   
ee_19                                      0.200818   
ee_2                                       0.156260   

            1_0002_Morse,:1_0003_best:1_0004_known  \
uniform_id                                           
ee_1                                      0.087358   
ee_12                                     0.228013   
ee_16                                     0.113263   
ee_19                                     0.166777   
ee_2                                      0.139261   

            1_0003_best:1_0004_known:1_0005_today  \
uniform_id                                          
ee_1                                     0.088408   
ee_12                                    0.128339   
ee_16                                    0.044434   
ee_19                                    0.161693   
ee_2                                     0.117522   

            1_0004_known:1_0005_today:1_0006_as  \
uniform_id                                        
ee_1                                   0.088408   
ee_12                                  0.128339   
ee_16                                  0.056444   
ee_19                                  0.131300   
ee_2                                   0.116214   

            1_0005_today:1_0006_as:1_0007_the  \
uniform_id                                      
ee_1                                 0.095128   
ee_12                                0.000000   
ee_16                                0.048563   
ee_19                                0.145336   
ee_2                                 0.077803   

            1_0006_as:1_0007_the:1_0008_inventor  \
uniform_id                                         
ee_1                                    0.093448   
ee_12                                   0.062975   
ee_16                                   0.082864   
ee_19                                   0.128979   
ee_2                                    0.110003   

            1_0007_the:1_0008_inventor:1_0009_of  \
uniform_id                                         
ee_1                                    0.121588   
ee_12                                   0.062975   
ee_16                                   0.070855   
ee_19                                   0.111848   
ee_2                                    0.081890   

            1_0008_inventor:1_0009_of:1_0010_Morse  \
uniform_id                                           
ee_1                                      0.113608   
ee_12                                     0.112052   
ee_16                                     0.099002   
ee_19                                     0.128205   
ee_2                                      0.125858   

            1_0009_of:1_0010_Morse:1_0011_Code  \
uniform_id                                       
ee_1                                  0.069929   
ee_12                                 0.080565   
ee_16                                 0.089695   
ee_19                                 0.173187   
ee_2                                  0.106407   

            1_0010_Morse:1_0011_Code:1_0012_and  \
uniform_id                                        
ee_1                                   0.082528   
ee_12                                  0.080565   
ee_16                                  0.112062   
ee_19                                  0.155172   
ee_2                                   0.106407   

            1_0011_Code:1_0012_and:1_0013_one  \
uniform_id                                      
ee_1                                 0.090088   
ee_12                                0.031488   
ee_16                                0.074458   
ee_19                                0.096817   
ee_2                                 0.062439   

           

In [25]:
df_baseline = map_unigrams(data_pivoted, random_mapper)
df_baseline

TF                                                    \
                  1         2         3         4         5         6    
uniform_id                                                               
ee_1        0.019642  0.051829  0.089650  0.078218  0.157119  0.017958   
ee_12       0.139974  0.060641  0.074686  0.079556  0.105134  0.042966   
ee_16       0.052630  0.079432  0.076681  0.060286  0.126553  0.000000   
ee_19       0.029294  0.038300  0.105339  0.096476  0.112754  0.047821   
ee_2        0.029010  0.048887  0.097763  0.085381  0.021679  0.023674   
...              ...       ...       ...       ...       ...       ...   
sp_59       0.041824  0.096489  0.091306  0.071348  0.049421  0.000000   
sp_60       0.018535  0.080802  0.083376  0.072170  0.028982  0.000000   
sp_62       0.010025  0.073572  0.081793  0.065224  0.035417  0.055981   
sp_63       0.027114  0.070624  0.065556  0.091386  0.024934  0.023110   
sp_8        0.028572  0.095580  0.081321  0.079449  0.039392  0.022639   

                                                                        \
                  7         8         9         10        11        12   
uniform_id                                                               
ee_1        0.033225  0.107998  0.041910  0.039704  0.098083  0.076166   
ee_12       0.010975  0.156105  0.115101  0.073954  0.066217  0.048835   
ee_16       0.025819  0.130616  0.036612  0.071442  0.041649  0.079156   
ee_19       0.031460  0.112754  0.030272  0.056615  0.086100  0.060081   
ee_2        0.000000  0.053295  0.044200  0.047612  0.060105  0.032037   
...              ...       ...       ...       ...       ...       ...   
sp_59       0.005650  0.119492  0.045901  0.056344  0.094026  0.049315   
sp_60       0.018389  0.126117  0.040600  0.093980  0.076392  0.046011   
sp_62       0.004647  0.081765  0.050378  0.041648  0.113418  0.061323   
sp_63       0.026682  0.107564  0.044728  0.091758  0.067810  0.048972   
sp_8        0.009779  0.086940  0.059518  0.070067  0.055360  0.078334   

                                                                        \
                  13        14        15        16        17        18   
uniform_id                                                               
ee_1        0.050553  0.061230  0.053681  0.031643  0.062176  0.024217   
ee_12       0.061831  0.046164  0.048601  0.019053  0.094312  0.030861   
ee_16       0.058929  0.040029  0.065063  0.092720  0.060645  0.019357   
ee_19       0.047788  0.046069  0.051451  0.045529  0.061469  0.027175   
ee_2        0.074430  0.041167  0.050166  0.060914  0.055191  0.038171   
...              ...       ...       ...       ...       ...       ...   
sp_59       0.062438  0.061409  0.032086  0.073488  0.057063  0.046989   
sp_60       0.057871  0.060525  0.034051  0.038025  0.062220  0.051020   
sp_62       0.032552  0.041659  0.061400  0.060561  0.042590  0.029173   
sp_63       0.069093  0.052060  0.055241  0.034188  0.067571  0.049914   
sp_8        0.050331  0.043651  0.043349  0.044423  0.063475  0.034641   

                                                                        \
                  19        20        21        22        23        24   
uniform_id                                                               
ee_1        0.088481  0.063382  0.058044  0.068145  0.068770  0.104847   
ee_12       0.071016  0.053593  0.084587  0.054958  0.031237  0.072779   
ee_16       0.078249  0.046543  0.048766  0.092591  0.049626  0.115409   
ee_19       0.051263  0.083042  0.058572  0.049049  0.059470  0.090066   
ee_2        0.062390  0.050471  0.048326  0.119644  0.037364  0.092798   
...              ...       ...       ...       ...       ...       ...   
sp_59       0.040714  0.079084  0.048155  0.091155  0.049859  0.087187   
sp_60       0.047717  0.072126  0.068107  0.063457  0.071081  0.090673   
sp_62       0.060180  0.066239  0.081048  0.056412  0.037299  0.086619   
sp_63       0.04941

#### SC (Apply tags mapper)

In [26]:
# POS
data_unigrams_POS = map_unigrams(data_pivoted, POS_mapper)
data_tf_bigrams_POS = map_bigrams(data_tf_bigrams, POS_mapper)
data_fp_bigrams_POS = map_bigrams(data_fp_bigrams, POS_mapper)
data_ff_bigrams_POS = map_bigrams(data_ff_bigrams, POS_mapper)
data_tf_trigrams_POS = map_trigrams(data_tf_trigrams, POS_mapper)
data_fp_trigrams_POS = map_trigrams(data_fp_trigrams, POS_mapper)
data_ff_trigrams_POS = map_trigrams(data_ff_trigrams, POS_mapper)

# PTB
data_unigrams_PTB = map_unigrams(data_pivoted, PTB_mapper)
data_tf_bigrams_PTB = map_bigrams(data_tf_bigrams, PTB_mapper)
data_fp_bigrams_PTB = map_bigrams(data_fp_bigrams, PTB_mapper)
data_ff_bigrams_PTB = map_bigrams(data_ff_bigrams, PTB_mapper)
data_tf_trigrams_PTB = map_trigrams(data_tf_trigrams, PTB_mapper)
data_fp_trigrams_PTB = map_trigrams(data_fp_trigrams, PTB_mapper)
data_ff_trigrams_PTB = map_trigrams(data_ff_trigrams, PTB_mapper)

# UD
data_unigrams_UD = map_unigrams(data_pivoted, UD_mapper)
data_tf_bigrams_UD = map_bigrams(data_tf_bigrams, UD_mapper)
data_fp_bigrams_UD = map_bigrams(data_fp_bigrams, UD_mapper)
data_ff_bigrams_UD = map_bigrams(data_ff_bigrams, UD_mapper)
data_tf_trigrams_UD = map_trigrams(data_tf_trigrams, UD_mapper)
data_fp_trigrams_UD = map_trigrams(data_fp_trigrams, UD_mapper)
data_ff_trigrams_UD = map_trigrams(data_ff_trigrams, UD_mapper)

### IC (apply tags mapper)

In [27]:
data_unigrams_IC = map_unigrams(data_pivoted, IC_mapper)
data_tf_bigrams_IC = map_bigrams(data_tf_bigrams, IC_mapper)
data_fp_bigrams_IC = map_bigrams(data_fp_bigrams, IC_mapper)
data_ff_bigrams_IC = map_bigrams(data_ff_bigrams, IC_mapper)
data_tf_trigrams_IC = map_trigrams(data_tf_trigrams, IC_mapper)
data_fp_trigrams_IC = map_trigrams(data_fp_trigrams, IC_mapper)
data_ff_trigrams_IC = map_trigrams(data_ff_trigrams, IC_mapper)

## Merge to one table

### WFC

Fix headers

In [28]:
add_header(data_tf_bigrams, 'TF_bi_WFC')
add_header(data_fp_bigrams, 'FP_bi_WFC')
add_header(data_ff_bigrams, 'FF_bi_WFC')

add_header(data_tf_trigrams, 'TF_tri_WFC')
add_header(data_fp_trigrams, 'FP_tri_WFC')
add_header(data_ff_trigrams, 'FF_tri_WFC')

In [29]:
# change unigram headers
data_pivoted = data_pivoted.rename(columns={'FP': 'FP_uni_WFC', 'FF':'FF_uni_WFC', 'TF': 'TF_uni_WFC'})

In [30]:
# check if all len same
len(data_fp_trigrams)

149

Merge

In [31]:
df_main = data_pivoted.merge(data_tf_bigrams, on = 'uniform_id')
df_main = df_main.merge(data_fp_bigrams, on = 'uniform_id')
df_main = df_main.merge(data_ff_bigrams, on = 'uniform_id')
df_main = df_main.merge(data_tf_trigrams, on = 'uniform_id')
df_main = df_main.merge(data_fp_trigrams, on = 'uniform_id')
df_main = df_main.merge(data_ff_trigrams, on = 'uniform_id')

In [32]:
df_main.shape

(149, 5364)

In [33]:
df_main.head()

TF_uni_WFC                                                      \
ia_id      1_0001_Samuel 1_0002_Morse, 1_0003_best 1_0004_known 1_0005_today   
uniform_id                                                                     
ee_1            0.059849      0.044309    0.000000     0.043049     0.045359   
ee_12           0.147014      0.099674    0.000000     0.128339     0.000000   
ee_16           0.011184      0.080913    0.000000     0.032350     0.012084   
ee_19           0.072944      0.062334    0.065539     0.038904     0.057250   
ee_2            0.055410      0.071429    0.029421     0.038411     0.049689   

                                                                        \
ia_id      1_0006_as 1_0007_the 1_0008_inventor 1_0009_of 1_0010_Morse   
uniform_id                                                               
ee_1        0.000000   0.049769        0.043679  0.028139     0.041789   
ee_12       0.000000   0.000000        0.062975  0.000000     0.049077   
ee_16       0.012009   0.024469        0.046386  0.000000     0.052616   
ee_19       0.035146   0.052940        0.040893  0.018015     0.069297   
ee_2        0.028114   0.000000        0.081890  0.000000     0.043969   

                                                                   \
ia_id      1_0011_Code 1_0012_and 1_0013_one 1_0014_of 1_0015_the   
uniform_id                                                          
ee_1          0.000000   0.040739   0.049349  0.000000   0.039899   
ee_12         0.031488   0.000000   0.000000  0.046037   0.036265   
ee_16         0.037079   0.022367   0.015012  0.000000   0.016138   
ee_19         0.085875   0.000000   0.010942  0.000000   0.016468   
ee_2          0.062439   0.000000   0.000000  0.000000   0.050997   

                                                                               \
ia_id      1_0016_inventors 1_0017_of 1_0018_the 1_0019_telegraph, 1_0020_was   
uniform_id                                                                      
ee_1               0.034649  0.039689   0.049139          0.051029   0.019110   
ee_12              0.019110  0.000000   0.000000          0.087296   0.000000   
ee_16              0.098401  0.015762   0.035427          0.262929   0.034302   
ee_19              0.034151  0.015363   0.000000          0.034593   0.021662   
ee_2               0.097581  0.000000   0.024845          0.053449   0.114090   

                                                                         \
ia_id      1_0021_originally  1_0022_a 1_0023_prominent 1_0024_painter.   
uniform_id                                                                
ee_1                0.062789  0.000000         0.143847        0.113818   
ee_12               0.143322  0.000000         0.105103        0.044300   
ee_16               0.029873  0.009532         0.065901        0.085266   
ee_19               0.080349  0.000000         0.115385        0.071950   
ee_2                0.074534  0.000000         0.059660        0.064073   

                                                                              \
ia_id      1_0025_While 1_0026_he 1_0027_was 1_0028_always 1_0029_interested   
uniform_id                                                                     
ee_1           0.040170  0.015013   0.102252      0.081152          0.063806   
ee_12          0.000000  0.032554   0.000000      0.000000          0.029271   
ee_16          0.022401  0.013286   0.010783      0.009771          0.060054   
ee_19          0.051067  0.006286   0.040048      0.015327          0.031996   
ee_2           0.000000  0.018334   0.000000      0.020200          0.018334   

                                                                  \
ia_id      1_0030_in 1_0031_technology 1_0032_and 1_0033_studied   
uniform_id                                                         
ee_1        0.000000          0.046054   0.000000       0.044938   
ee_12       0.000000          0.023116   0.000000       0.040624

### SC

Fix headers

In [34]:
# POS
data_unigrams_POS = data_unigrams_POS.rename(columns={'FP': 'FP_uni_POS', 'FF':'FF_uni_POS', 'TF': 'TF_uni_POS'})
add_header(data_tf_bigrams_POS, 'TF_bi_POS')
add_header(data_fp_bigrams_POS, 'FP_bi_POS')
add_header(data_ff_bigrams_POS, 'FF_bi_POS')
add_header(data_tf_trigrams_POS, 'TF_tri_POS')
add_header(data_fp_trigrams_POS, 'FP_tri_POS')
add_header(data_ff_trigrams_POS, 'FF_tri_POS')

# PTB
data_unigrams_PTB = data_unigrams_PTB.rename(columns={'FP': 'FP_uni_PTB', 'FF':'FF_uni_PTB', 'TF': 'TF_uni_PTB'})
add_header(data_tf_bigrams_PTB, 'TF_bi_PTB')
add_header(data_fp_bigrams_PTB, 'FP_bi_PTB')
add_header(data_ff_bigrams_PTB, 'FF_bi_PTB')
add_header(data_tf_trigrams_PTB, 'TF_tri_PTB')
add_header(data_fp_trigrams_PTB, 'FP_tri_PTB')
add_header(data_ff_trigrams_PTB, 'FF_tri_PTB')

# UD
data_unigrams_UD = data_unigrams_UD.rename(columns={'FP': 'FP_uni_UD', 'FF':'FF_uni_UD', 'TF': 'TF_uni_UD'})
add_header(data_tf_bigrams_UD, 'TF_bi_UD')
add_header(data_fp_bigrams_UD, 'FP_bi_UD')
add_header(data_ff_bigrams_UD, 'FF_bi_UD')
add_header(data_tf_trigrams_UD, 'TF_tri_UD')
add_header(data_fp_trigrams_UD, 'FP_tri_UD')
add_header(data_ff_trigrams_UD, 'FF_tri_UD')

Merge

In [35]:
# POS
df_main_POS = data_unigrams_POS.merge(data_tf_bigrams_POS, on = 'uniform_id')
df_main_POS = df_main_POS.merge(data_fp_bigrams_POS, on = 'uniform_id')
df_main_POS = df_main_POS.merge(data_ff_bigrams_POS, on = 'uniform_id')
df_main_POS = df_main_POS.merge(data_tf_trigrams_POS, on = 'uniform_id')
df_main_POS = df_main_POS.merge(data_fp_trigrams_POS, on = 'uniform_id')
df_main_POS = df_main_POS.merge(data_ff_trigrams_POS, on = 'uniform_id')

# PTB
df_main_PTB = data_unigrams_PTB.merge(data_tf_bigrams_PTB, on = 'uniform_id')
df_main_PTB = df_main_PTB.merge(data_fp_bigrams_PTB, on = 'uniform_id')
df_main_PTB = df_main_PTB.merge(data_ff_bigrams_PTB, on = 'uniform_id')
df_main_PTB = df_main_PTB.merge(data_tf_trigrams_PTB, on = 'uniform_id')
df_main_PTB = df_main_PTB.merge(data_fp_trigrams_PTB, on = 'uniform_id')
df_main_PTB = df_main_PTB.merge(data_ff_trigrams_PTB, on = 'uniform_id')

# UD
df_main_UD = data_unigrams_UD.merge(data_tf_bigrams_UD, on = 'uniform_id')
df_main_UD = df_main_UD.merge(data_fp_bigrams_UD, on = 'uniform_id')
df_main_UD = df_main_UD.merge(data_ff_bigrams_UD, on = 'uniform_id')
df_main_UD = df_main_UD.merge(data_tf_trigrams_UD, on = 'uniform_id')
df_main_UD = df_main_UD.merge(data_fp_trigrams_UD, on = 'uniform_id')
df_main_UD = df_main_UD.merge(data_ff_trigrams_UD, on = 'uniform_id')

To one table

In [36]:
df_main_SC = df_main_POS.merge(df_main_PTB, on = 'uniform_id')
df_main_SC = df_main_SC.merge(df_main_UD, on = 'uniform_id')

### IC

In [37]:
# Fix headers
data_unigrams_IC = data_unigrams_IC.rename(columns={'FP': 'FP_uni_IC', 'FF':'FF_uni_IC', 'TF': 'TF_uni_IC'})
add_header(data_tf_bigrams_IC, 'TF_bi_IC')
add_header(data_fp_bigrams_IC, 'FP_bi_IC')
add_header(data_ff_bigrams_IC, 'FF_bi_IC')
add_header(data_tf_trigrams_IC, 'TF_tri_IC')
add_header(data_fp_trigrams_IC, 'FP_tri_IC')
add_header(data_ff_trigrams_IC, 'FF_tri_IC')

# Merge
df_main_IC = data_unigrams_IC.merge(data_tf_bigrams_IC, on = 'uniform_id')
df_main_IC = df_main_IC.merge(data_fp_bigrams_IC, on = 'uniform_id')
df_main_IC = df_main_IC.merge(data_ff_bigrams_IC, on = 'uniform_id')
df_main_IC = df_main_IC.merge(data_tf_trigrams_IC, on = 'uniform_id')
df_main_IC = df_main_IC.merge(data_fp_trigrams_IC, on = 'uniform_id')
df_main_IC = df_main_IC.merge(data_ff_trigrams_IC, on = 'uniform_id')

## Save

### WFC

In [38]:
df_main.to_pickle("../data/df_uni_bi_tri_normalized.pickle")

### SC

In [39]:
df_main_SC.to_pickle("../data/df_uni_bi_tri_normalized_SC.pickle")

### IC

In [40]:
df_main_IC.to_pickle("../data/df_uni_bi_tri_normalized_IC.pickle")

### Baseline

In [41]:
df_baseline.to_pickle("../data/df_baseline.pickle")

In [42]:
df_main_IC

TF_uni_IC                                                    \
                   1         2         3         4         5         6   
uniform_id                                                               
ee_1        0.009998  0.023192  0.029079  0.046060  0.070003  0.067079   
ee_12       0.002560  0.034087  0.022358  0.045747  0.067751  0.066046   
ee_16       0.013617  0.023633  0.025056  0.045608  0.054183  0.074122   
ee_19       0.010764  0.025033  0.029804  0.047063  0.068039  0.073395   
ee_2        0.000000  0.025965  0.027581  0.043181  0.060465  0.075369   
...              ...       ...       ...       ...       ...       ...   
sp_59       0.010738  0.020291  0.025432  0.041301  0.070956  0.081402   
sp_60       0.011993  0.013818  0.021407  0.047784  0.075721  0.081203   
sp_62       0.020808  0.024796  0.026496  0.031354  0.067683  0.067646   
sp_63       0.009323  0.017545  0.026514  0.039955  0.059266  0.078241   
sp_8        0.009472  0.019974  0.031329  0.047456  0.067005  0.064643   

                                                                        \
                   7         8         9        10        11        12   
uniform_id                                                               
ee_1        0.084932  0.082588  0.115936  0.100668  0.115397  0.121597   
ee_12       0.094801  0.090759  0.101883  0.075070  0.113397  0.124303   
ee_16       0.093430  0.087593  0.119222  0.124316  0.101819  0.109499   
ee_19       0.084757  0.072630  0.100882  0.096836  0.099269  0.126899   
ee_2        0.090275  0.095223  0.107335  0.130260  0.113137  0.100488   
...              ...       ...       ...       ...       ...       ...   
sp_59       0.092447  0.089793  0.092017  0.084223  0.109295  0.126649   
sp_60       0.095903  0.096673  0.083114  0.098542  0.107508  0.091440   
sp_62       0.090572  0.084896  0.102117  0.118177  0.111569  0.158084   
sp_63       0.091618  0.092131  0.107391  0.099869  0.117320  0.138307   
sp_8        0.087556  0.080641  0.096580  0.093272  0.111691  0.122166   

                               FP_uni_IC                                \
                  13        15         1         2         3         4   
uniform_id                                                               
ee_1        0.297291  0.064955  0.009998  0.022705  0.024485  0.036597   
ee_12       0.392951  0.054384  0.001817  0.030677  0.019220  0.033415   
ee_16       0.416558  0.069280  0.013617  0.022257  0.022368  0.037166   
ee_19       0.372850  0.253511  0.010764  0.021287  0.026412  0.037573   
ee_2        0.220138  0.123278  0.000000  0.024884  0.025929  0.041512   
...              ...       ...       ...       ...       ...       ...   
sp_59       0.165209  0.104517  0.010738  0.020291  0.025074  0.039189   
sp_60       0.147949  0.084067  0.011993  0.011729  0.019983  0.041489   
sp_62       0.260103  0.070659  0.020808  0.022745  0.023956  0.029502   
sp_63       0.288008  0.055775  0.008526  0.011151  0.017281  0.018780   
sp_8        0.242291  0.099036  0.007482  0.019043  0.027202  0.038551   

                                                                        \
                   5         6         7         8         9        10   
uniform_id                                                               
ee_1        0.050571  0.049663  0.071821  0.062240  0.087566  0.072621   
ee_12       0.051459  0.059238  0.081112  0.054227  0.072271  0.060053   
ee_16       0.043472  0.058541  0.078749  0.066346  0.085305  0.070803   
ee_19       0.047265  0.052501  0.063639  0.052292  0.066337  0.061718   
ee_2        0.057092  0.062381  0.081138  0.078140  0.089577  0.118172   
...              ...       ...       ...       ...       ...       ...   
sp_59       0.062220  0.072636  0.088699  0.080040  0.078676  0.084223   
sp_60       0.064110  0.073378  0.083332  0.079429  0.076288  0.068339   
sp_62       0.056303  0.060591  0.069707  0.064145  0.089406  0.084217   
sp_63       

In [45]:
df_main.columns.shape

(5364,)

In [49]:
df_main["TF_tri_WFC"]

ia_id       1_0001_Samuel:1_0002_Morse,:1_0003_best  \
uniform_id                                            
ee_1                                       0.104158   
ee_12                                      0.246688   
ee_16                                      0.092096   
ee_19                                      0.200818   
ee_2                                       0.156260   
...                                             ...   
sp_59                                      0.156736   
sp_60                                      0.302030   
sp_62                                      0.359888   
sp_63                                      0.120984   
sp_8                                       0.131667   

ia_id       1_0002_Morse,:1_0003_best:1_0004_known  \
uniform_id                                           
ee_1                                      0.087358   
ee_12                                     0.228013   
ee_16                                     0.113263   
ee_19                                     0.166777   
ee_2                                      0.139261   
...                                            ...   
sp_59                                     0.158172   
sp_60                                     0.211439   
sp_62                                     0.421550   
sp_63                                     0.148316   
sp_8                                      0.202726   

ia_id       1_0003_best:1_0004_known:1_0005_today  \
uniform_id                                          
ee_1                                     0.088408   
ee_12                                    0.128339   
ee_16                                    0.044434   
ee_19                                    0.161693   
ee_2                                     0.117522   
...                                           ...   
sp_59                                    0.082556   
sp_60                                    0.128413   
sp_62                                    0.115409   
sp_63                                    0.120078   
sp_8                                     0.235802   

ia_id       1_0004_known:1_0005_today:1_0006_as  \
uniform_id                                        
ee_1                                   0.088408   
ee_12                                  0.128339   
ee_16                                  0.056444   
ee_19                                  0.131300   
ee_2                                   0.116214   
...                                         ...   
sp_59                                  0.082556   
sp_60                                  0.061070   
sp_62                                  0.117962   
sp_63                                  0.120078   
sp_8                                   0.197910   

ia_id       1_0005_today:1_0006_as:1_0007_the  \
uniform_id                                      
ee_1                                 0.095128   
ee_12                                0.000000   
ee_16                                0.048563   
ee_19                                0.145336   
ee_2                                 0.077803   
...                                       ...   
sp_59                                0.088299   
sp_60                                0.080812   
sp_62                                0.064981   
sp_63                                0.080311   
sp_8                                 0.082417   

ia_id       1_0006_as:1_0007_the:1_0008_inventor  \
uniform_id                                         
ee_1                                    0.093448   
ee_12                                   0.062975   
ee_16                                   0.082864   
ee_19                                   0.128979   
ee_2                                    0.110003   
...                                          ...   
sp_59                                   0.090213   
sp_60                                   0.092620   
sp_62                                   0.113111   
sp_63            

##### 